## Data was loaded using python and Temp view was created to query using SQL statements

In [0]:
from pyspark.sql import functions as F
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


In [0]:
dbutils.fs.ls('FileStore/tables/')

Out[2]: [FileInfo(path='dbfs:/FileStore/tables/creditcard-1.csv', name='creditcard-1.csv', size=150828752, modificationTime=1733142386000),
 FileInfo(path='dbfs:/FileStore/tables/creditcard.csv', name='creditcard.csv', size=150828752, modificationTime=1732695303000),
 FileInfo(path='dbfs:/FileStore/tables/train_identity.csv', name='train_identity.csv', size=26529680, modificationTime=1733142316000),
 FileInfo(path='dbfs:/FileStore/tables/train_transaction.csv', name='train_transaction.csv', size=683351067, modificationTime=1733142468000)]

In [0]:
train_identity_df = spark.read.option("header", "true").csv('/FileStore/tables/train_identity.csv').toPandas()
train_transaction_df = spark.read.option("header", "true").csv('/FileStore/tables/train_transaction.csv').toPandas()
data = pd.merge(train_transaction_df, train_identity_df, on='TransactionID', how='left')


# Convert TransactionDT to datetime
reference_date = pd.Timestamp("2017-01-01")  # Assuming a reference date
data['transaction_time'] = data['TransactionDT'].astype(int).apply(lambda x: reference_date + pd.Timedelta(seconds=x))
data['transaction_date'] = data['transaction_time'].dt.date
data['transaction_hour'] = data['transaction_time'].dt.hour
data['transaction_month'] = data['transaction_time'].dt.month_name()
data['transaction_day'] = data['transaction_time'].dt.day_name()

spark_df = spark.createDataFrame(data)
        

In [0]:
# Register the Spark DataFrame as a temporary SQL table

In [0]:
spark_df.createOrReplaceTempView("temp_data")

In [0]:
## Window Functions

In [0]:
# SQL Query for Hourly Fraud Distribution
hourly_fraud_query = """
SELECT DISTINCT
    transaction_hour,
    COUNT(*) OVER (PARTITION BY transaction_hour) as total_transactions,
    SUM(CASE WHEN isFraud = 1 THEN 1 ELSE 0 END) OVER (PARTITION BY transaction_hour) as fraud_count,
    ROUND(100.0 * SUM(CASE WHEN isFraud = 1 THEN 1 ELSE 0 END) OVER (PARTITION BY transaction_hour) / COUNT(*) OVER (PARTITION BY transaction_hour), 2) as fraud_percentage,
    AVG(TransactionAmt) OVER (PARTITION BY transaction_hour) as avg_transaction_amount
FROM temp_data

ORDER BY fraud_count DESC;
"""

# Execute and display the results

# GROUP BY transaction_hour
hourly_fraud = spark.sql(hourly_fraud_query)
display(hourly_fraud)


transaction_hour total_transactions fraud_count fraud_percentage avg_transaction_amount 23 39949 1478 3.70 130.15982675414295 18 41639 1467 3.52 147.58654898055352 19 42115 1463 3.47 143.64452344773375 20 41782 1432 3.43 144.5583549854311 21 41641 1416 3.40 140.91608393173277 22 41139 1345 3.27 136.06918238171454 17 40723 1284 3.15 151.04254202787877 0 37795 1186 3.14 123.30986270673922 16 38698 1142 2.95 145.52923393977036 1 32797 1027 3.13 116.0284466872262 2 26732 1002 3.75 111.33219665570928 15 33859 860 2.54 150.365576833368 3 20802 797 3.83 106.60173098739638 4 14839 770 5.19 102.96102028437535 14 28328 686 2.42 146.0958123764748 5 9701 682 7.03 105.26336377692363 6 6007 467 7.77 105.71876344264908 13 20315 465 2.29 144.0079686930933 7 3704 393 10.61 113.85700836933245 12 12451 379 3.04 131.09095518431084 11 6827 265 3.88 122.9790055661296 8 2591 241 9.30 125.439313006563 9 2479 223 9.00 144.51666438080088 10 3627 193 5.32 132.43595919492978

In [0]:
# SQL Query for Moving Averages and Cumulative Fraud Analysis
moving_avg_query = """
WITH daily_fraud AS (
    SELECT 
        transaction_date,
        SUM(CASE WHEN isFraud = 1 THEN 1 ELSE 0 END) as daily_fraud_count,
        SUM(CASE WHEN isFraud = 1 THEN TransactionAmt ELSE 0 END) as daily_fraud_amount
    FROM temp_data
    GROUP BY transaction_date
)
SELECT 
    transaction_date,
    daily_fraud_count,
    daily_fraud_amount,
    AVG(daily_fraud_count) OVER (ORDER BY transaction_date ROWS BETWEEN 7 PRECEDING AND CURRENT ROW) as rolling_7day_fraud_count,
    AVG(daily_fraud_amount) OVER (ORDER BY transaction_date ROWS BETWEEN 7 PRECEDING AND CURRENT ROW) as rolling_7day_fraud_amount,
    SUM(daily_fraud_count) OVER (ORDER BY transaction_date) as cumulative_fraud_count,
    SUM(daily_fraud_amount) OVER (ORDER BY transaction_date) as cumulative_fraud_amount
FROM daily_fraud
ORDER BY transaction_date
"""

# Execute and display the results
moving_avg = spark.sql(moving_avg_query)
display(moving_avg)


transaction_date daily_fraud_count daily_fraud_amount rolling_7day_fraud_count rolling_7day_fraud_amount cumulative_fraud_count cumulative_fraud_amount 2017-01-02 112 20337.144 112.0 20337.144 112 20337.144 2017-01-03 123 15359.606999999995 117.5 17848.3755 235 35696.751 2017-01-04 92 14254.337 109.0 16650.362666666664 327 49951.087999999996 2017-01-05 115 14120.447 110.5 16017.883749999999 442 64071.534999999996 2017-01-06 127 16692.721 113.8 16152.8512 569 80764.256 2017-01-07 99 12869.08 111.33333333333333 15605.555999999999 668 93633.336 2017-01-08 136 21670.363000000027 114.85714285714286 16471.957000000002 804 115303.69900000002 2017-01-09 93 13508.151999999998 112.125 16101.481375000003 897 128811.85100000002 2017-01-10 119 13106.597999999994 113.0 15197.663125000003 1016 141918.44900000002 2017-01-11 90 12709.721000000001 108.875 14866.427375000005 1106 154628.17 2017-01-12 123 21725.539000000004 112.75 15800.327625000004 1229 176353.70900000003 2017-01-13 84 14710.558 108.875 15874.091500000004 1313 191064.26700000002 2017-01-14 82 10975.380000000001 103.25 15159.423875000006 1395 202039.64700000003 2017-01-15 126 15782.409000000001 106.625 15523.590000000006 1521 217822.05600000004 2017-01-16 143 16438.68099999999 107.5 14869.62975 1664 234260.73700000002 2017-01-17 70 7279.535 104.625 14091.052625 1734 241540.27200000003 2017-01-18 126 14338.320000000002 105.5 14245.017875000001 1860 255878.59200000003 2017-01-19 161 19745.874000000014 114.375 15124.537000000004 2021 275624.4660000001 2017-01-20 118 13647.861000000003 113.75 14114.827250000002 2139 289272.32700000005 2017-01-21 135 20877.602 120.125 14885.707750000001 2274 310149.92900000006 2017-01-22 116 11047.986 124.375 14894.783500000001 2390 321197.91500000004 2017-01-23 147 18677.98300000001 127.0 15256.730250000002 2537 339875.89800000004 2017-01-24 106 15191.023999999996 122.375 15100.773125000003 2643 355066.922 2017-01-25 76 11902.088 123.125 15678.592250000003 2719 366969.01 2017-01-26 63 5965.497999999999 115.25 14631.989500000001 2782 372934.50800000003 2017-01-27 82 12609.165 105.375 13739.900875 2864 385543.673 2017-01-28 100 14725.043999999996 103.125 13874.548749999998 2964 400268.717 2017-01-29 150 22367.33000000001 105.0 14060.764750000002 3114 422636.047 2017-01-30 129 16953.839000000007 106.625 14798.996375000002 3243 439589.88600000006 2017-01-31 158 22107.92000000002 108.0 15227.738500000003 3401 461697.8060000001 2017-02-01 149 18823.939999999988 113.375 15681.853000000001 3550 480521.7460000001 2017-02-02 51 6477.429999999999 110.25 15003.770750000001 3601 486999.1760000001 2017-02-03 123 18623.234999999997 117.75 16585.987875000003 3724 505622.4110000001 2017-02-04 159 22765.200000000004 127.375 17855.492250000003 3883 528387.611 2017-02-05 120 15812.873000000003 129.875 17991.470875000003 4003 544200.484 2017-02-06 135 20959.428999999996 128.0 17815.48325 4138 565159.9130000001 2017-02-07 126 24458.921000000013 127.625 18753.6185 4264 589618.834 2017-02-08 110 13548.031999999997 121.625 17683.6325 4374 603166.866 2017-02-09 117 15022.658000000016 117.625 17208.472250000006 4491 618189.5240000001 2017-02-10 109 16653.409 124.875 18480.469625000005 4600 634842.9330000001 2017-02-11 121 18989.125000000007 124.625 18526.205875000003 4721 653832.0580000001 2017-02-12 85 12384.086999999994 115.375 17228.56675 4806 666216.145 2017-02-13 160 15913.498000000003 120.375 17241.144875 4966 682129.643 2017-02-14 119 18996.227 118.375 16995.744625000003 5085 701125.87 2017-02-15 100 11489.538 115.125 15374.571750000003 5185 712615.408 2017-02-16 117 17005.305 116.0 15806.730875000001 5302 729620.7130000001 2017-02-17 91 12495.116000000002 112.75 15490.788125000003 5393 742115.8290000001 2017-02-18 115 14594.982000000004 113.5 15233.484750000001 5508 756710.8110000001 2017-02-19 121 14391.142 113.5 14658.736875000002 5629 771101.9530000001 2017-02-20 175 20959.673 124.75 15730.685125000002 5804 792061.626 2017-02-21 148 21140.629999999994 123.25 16384.0

In [0]:
# SQL Query for Rolling Average of Transaction Amounts
query_rolling_avg = """
SELECT transaction_time, transaction_date, transaction_hour,transaction_month, transaction_day,
       AVG(TransactionAmt) OVER (PARTITION BY transaction_day ORDER BY transaction_date ASC ROWS BETWEEN 2 PRECEDING AND CURRENT ROW) AS rolling_avg_amt
FROM temp_data
"""

rolling_avg_data = spark.sql(query_rolling_avg)
display(rolling_avg_data)


transaction_time transaction_date transaction_hour transaction_month transaction_day rolling_avg_amt 2017-01-03T00:00:07.000+0000 2017-01-03 0 January Tuesday 150.95 2017-01-03T00:00:07.000+0000 2017-01-03 0 January Tuesday 121.975 2017-01-03T00:00:18.000+0000 2017-01-03 0 January Tuesday 86.31666666666666 2017-01-03T00:00:57.000+0000 2017-01-03 0 January Tuesday 75.0 2017-01-03T00:00:59.000+0000 2017-01-03 0 January Tuesday 54.31666666666666 2017-01-03T00:01:06.000+0000 2017-01-03 0 January Tuesday 67.64666666666666 2017-01-03T00:01:18.000+0000 2017-01-03 0 January Tuesday 45.31333333333333 2017-01-03T00:01:41.000+0000 2017-01-03 0 January Tuesday 65.66333333333334 2017-01-03T00:02:31.000+0000 2017-01-03 0 January Tuesday 66.64999999999999 2017-01-03T00:02:35.000+0000 2017-01-03 0 January Tuesday 57.63999999999999 2017-01-03T00:02:41.000+0000 2017-01-03 0 January Tuesday 63.076666666666675 2017-01-03T00:03:11.000+0000 2017-01-03 0 January Tuesday 85.42666666666666 2017-01-03T00:03:18.000+0000 2017-01-03 0 January Tuesday 226.10333333333332 2017-01-03T00:03:45.000+0000 2017-01-03 0 January Tuesday 206.66666666666666 2017-01-03T00:04:23.000+0000 2017-01-03 0 January Tuesday 184.3166666666667 2017-01-03T00:04:30.000+0000 2017-01-03 0 January Tuesday 81.64666666666666 2017-01-03T00:04:32.000+0000 2017-01-03 0 January Tuesday 111.64666666666666 2017-01-03T00:04:37.000+0000 2017-01-03 0 January Tuesday 111.99666666666667 2017-01-03T00:05:32.000+0000 2017-01-03 0 January Tuesday 79.98333333333333 2017-01-03T00:05:34.000+0000 2017-01-03 0 January Tuesday 46.31666666666666 2017-01-03T00:05:52.000+0000 2017-01-03 0 January Tuesday 35.65 2017-01-03T00:06:15.000+0000 2017-01-03 0 January Tuesday 353.3333333333333 2017-01-03T00:06:24.000+0000 2017-01-03 0 January Tuesday 348.6666666666667 2017-01-03T00:06:29.000+0000 2017-01-03 0 January Tuesday 351.3333333333333 2017-01-03T00:06:40.000+0000 2017-01-03 0 January Tuesday 141.83333333333334 2017-01-03T00:06:54.000+0000 2017-01-03 0 January Tuesday 190.5 2017-01-03T00:06:54.000+0000 2017-01-03 0 January Tuesday 187.16666666666666 2017-01-03T00:06:59.000+0000 2017-01-03 0 January Tuesday 98.04066666666667 2017-01-03T00:07:00.000+0000 2017-01-03 0 January Tuesday 87.70733333333334 2017-01-03T00:07:01.000+0000 2017-01-03 0 January Tuesday 112.70733333333334 2017-01-03T00:07:31.000+0000 2017-01-03 0 January Tuesday 105.66666666666667 2017-01-03T00:07:35.000+0000 2017-01-03 0 January Tuesday 75.33333333333333 2017-01-03T00:07:38.000+0000 2017-01-03 0 January Tuesday 75.33333333333333 2017-01-03T00:07:43.000+0000 2017-01-03 0 January Tuesday 69.33333333333333 2017-01-03T00:07:45.000+0000 2017-01-03 0 January Tuesday 92.0 2017-01-03T00:07:55.000+0000 2017-01-03 0 January Tuesday 75.33333333333333 2017-01-03T00:08:21.000+0000 2017-01-03 0 January Tuesday 167.33333333333334 2017-01-03T00:08:24.000+0000 2017-01-03 0 January Tuesday 135.98666666666665 2017-01-03T00:08:27.000+0000 2017-01-03 0 January Tuesday 450.65333333333336 2017-01-03T00:08:30.000+0000 2017-01-03 0 January Tuesday 346.4866666666667 2017-01-03T00:08:34.000+0000 2017-01-03 0 January Tuesday 375.0 2017-01-03T00:08:45.000+0000 2017-01-03 0 January Tuesday 60.333333333333336 2017-01-03T00:09:05.000+0000 2017-01-03 0 January Tuesday 64.5 2017-01-03T00:09:15.000+0000 2017-01-03 0 January Tuesday 323.0 2017-01-03T00:09:48.000+0000 2017-01-03 0 January Tuesday 323.0 2017-01-03T00:09:53.000+0000 2017-01-03 0 January Tuesday 361.31666666666666 2017-01-03T00:10:17.000+0000 2017-01-03 0 January Tuesday 89.98333333333333 2017-01-03T00:10:28.000+0000 2017-01-03 0 January Tuesday 165.98333333333332 2017-01-03T00:10:32.000+0000 2017-01-03 0 January Tuesday 149.33333333333334 2017-01-03T00:10:34.000+0000 2017-01-03 0 January Tuesday 155.0 2017-01-03T00:10:36.000+0000 2017-01-03 0 January Tuesday 210.66666666666666 2017-01-03T00:10:59.000+0000 2017-01-03 0 January Tuesday 189.0 2017-01-03T00:11:03.000+0000 2017-01-03 0 January Tuesday 168.338 2017-01-

In [0]:
# SQL Query for Cumulative Sum of Transaction Amounts
query_cumulative_sum = """
SELECT transaction_time, transaction_date, transaction_hour,transaction_month, transaction_day,
       SUM(TransactionAmt) OVER (PARTITION BY transaction_day ORDER BY transaction_date ASC) AS cumulative_sum_amt
FROM temp_data
"""

cumulative_sum_data = spark.sql(query_cumulative_sum)
display(cumulative_sum_data)


transaction_time transaction_date transaction_hour transaction_month transaction_day cumulative_sum_amt 2017-01-03T00:00:07.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:00:07.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:00:18.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:00:57.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:00:59.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:01:06.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:01:18.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:01:41.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:02:31.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:02:35.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:02:41.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:03:11.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:03:18.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:03:45.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:04:23.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:04:30.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:04:32.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:04:37.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:05:32.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:05:34.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:05:52.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:15.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:24.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:29.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:40.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:54.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:54.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:06:59.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:00.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:01.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:31.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:35.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:38.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:43.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:45.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:07:55.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:21.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:24.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:27.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:30.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:34.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:08:45.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:09:05.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:09:15.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:09:48.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:09:53.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:17.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:28.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:32.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:34.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:36.000+0000 2017-01-03 0 January Tuesday 453400.0130000047 2017-01-03T00:10:59.